In [1]:
import Pkg; Pkg.activate("../scratch")

"/home/chfin/Uni/phd/code/schemata_code/scratch/Project.toml"

In [2]:
#using Interact
#using Revise # install if necessary
using DigitalMusicology
using MusicologyPlots
#using DataFrames
#using GLM

┌ Info: Recompiling stale cache file /home/chfin/.julia/compiled/v1.1/DigitalMusicology/ngEmt.ji for DigitalMusicology [2c2a18ac-9fc9-11e8-3acf-35f06862b736]
└ @ Base loading.jl:1184
┌ Info: Recompiling stale cache file /home/chfin/.julia/compiled/v1.1/MusicologyPlots/EFGox.ji for MusicologyPlots [c9d89ec8-a6c4-11e8-1629-537f3e81f650]
└ @ Base loading.jl:1184


HTML{String}("<script>\n// Immediately-invoked-function-expression to avoid global variables.\n(function() {\n    var warning_div = document.getElementById(\"webio-warning-1727035851352576127\");\n    var hide = function () {\n        var script = document.getElementById(\"webio-setup-6294824219501630525\");\n        var parent = script && script.parentElement;\n        var grandparent = parent && parent.parentElement;\n        if (grandparent) {\n            grandparent.style.display = \"none\";\n        }\n        warning_div.style.display = \"none\";\n    };\n    if (typeof Jupyter !== \"undefined\") {\n        console.log(\"WebIO detected Jupyter notebook environment.\");\n        // Jupyter notebook.\n        var extensions = (\n            Jupyter\n            && Jupyter.notebook.config.data\n            && Jupyter.notebook.config.data.load_extensions\n        );\n        if (extensions && extensions[\"webio/main\"]) {\n            // Extension already loaded.\n            console.log(\"Jupyter WebIO nbextension detected; not loading ad-hoc.\");\n            hide();\n            return;\n        }\n        console.warn(\"Loading WebIO Jupyter extension on an ad-hoc basis. Consider enabling the WebIO nbextension for a stabler experience (this should happen automatically when building WebIO).\");\n        require([\"/assetserver/3f760c2c60d10c8704d427861ed9fa3f4dca0fa9-dist/main.js\"], function (webIOModule) {\n            webIOModule.load_ipython_extension();\n        });\n        warning_div.innerHTML = \"<strong>Loading WebIO Jupyter extension on an ad-hoc basis. Consider enabling the WebIO nbextension for a stabler experience (this should happen automatically when building WebIO).</strong>\";\n    } else if (window.location.pathname.includes(\"/lab\")) {\n        // Guessing JupyterLa\n        console.log(\"Jupyter Lab detected; make sure the @webio/jupyter-lab-provider labextension is installed.\");\n        hide();\n        return;\n    }\n})();\n\n</script>\n<div\n    id=\"webio-warning-1727035851352576127\"\n    class=\"output_text output_stderr\"\n    style=\"padding: 1em; font-weight: bold;\"\n>\n    Unable to load WebIO. Please make sure WebIO works for your Jupyter client.\n    <!-- TODO: link to installation docs. -->\n</div>\n")

In [3]:
include("../src/polygrams.jl")

Main.Polygrams

In [4]:
#corpuspath = "/home/chfin/Uni/phd/data/dcml_corpora/annotations/Mozart-Sonatas/Schema Annotations/musicxml"
corpuspath = "/home/chfin/dateien/dev/haskell/haskell-musicology/musicology-musicxml/testdata/"
#corpuspath = "/home/chfin/Uni/phd/data/dcml_corpora/annotations/Couperin-L'art de toucher/"
DigitalMusicology.usedir(corpuspath)

DigitalMusicology.Corpora.Directory.DirCorpus("/home/chfin/dateien/dev/haskell/haskell-musicology/musicology-musicxml/testdata/", ["n03"])

In [5]:
#pieceid = "m9836_4"
#pieceid = "K281-3"
pieceid = "n03"
notes = getpiece(pieceid, :notes, :musicxml; type=:notes, keepids=false);
timesigs = getpiece(pieceid, :timesigs, :musicxml, unfold=false);
barlen = duration(content(timesigs[1][1]))
xml = getpiece(pieceid, :xml, :musicxml; keepids=false);

In [6]:
fonte2v = Polygrams.schemarep([sic(0,1) sic(4,7); sic(1,2) sic(3,5);
                               sic(-1,-1) sic(3,5); sic(0,0) sic(2,4)]; sortstages=false)
#fonte2v = @midi [[0, 6], [1, 4], [10, 4], [11, 3]]

4×2 Array{SpelledIC,2}:
 P1  d5
 m2  d4
 m7  d4
 d1  m3

In [7]:
beatfactor = denominator(content(timesigs[1][1]))
featurefs = [
    poly -> beatfactor * Polygrams.totalduration(poly), # duration
    Polygrams.voicedist,                                # voice dist
    poly -> beatfactor * Polygrams.instageskip(poly)    # stage skip
    #, poly -> Polygrams.polymweight(poly, timesigs) # metric weight
]
featureweights = [1, -1, -2] # maaaaaagic
featurekeys = [:dur, :vdist, :skip]
#modelform = @formula(label ~ dur + vdist + skip)

3-element Array{Symbol,1}:
 :dur  
 :vdist
 :skip 

In [8]:
polyitr = Polygrams.schemamatches(notes, [fonte2v], barlen, barlen);
polys = collect(polyitr);
length(polys)

366

In [9]:
sorted = Polygrams.sortbyheuristics(polys, featurefs, featureweights);
scores = Dict(poly => Polygrams.rate(poly, featurefs, featureweights) for poly in polys);

In [10]:
matcherwdg = Polygrams.matchinteractivewdg(notes, sorted, xml)
matcherwdg

WebIO.Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{DOM}(DOM(:html, :div), Any[Node{DOM}(DOM(:html, :div), Any[Node{DOM}(DOM(:html, :div), Any[Node{DOM}(DOM(:html, :div), Any["Match No."], Dict{Symbol,Any}(:className=>"level-item"), 1), Node{DOM}(DOM(:html, :div), Any[Node{DOM}(DOM(:html, :div), Any[Scope("knockout-component-8b327201-37a2-4b24-a15b-14a8838dff89", Node{DOM}(DOM(:html, :button), Any["Previous"], Dict{Symbol,Any}(:attributes=>Dict{Any,Any}("data-bind"=>"click: function (){this.clicks(this.clicks()+1)}, css: {'is-loading' : loading}"),:className=>"is-medium button is-primary",:style=>Dict{String,Any}()), 1), Dict{String,Tuple{Observables.AbstractObservable,Union{Nothing, Bool}}}("loading"=>(Observable{Bool} with 1 listeners. Value:
false, nothing),"clicks"=>(Observable{Int64} with 2 listeners. Value:
0, nothing)), Set(String[]), nothing, WebIO.Asset[Asset("js", "knockout", "/home/chfin/.julia/packages/Knockout/JE2Yq/src/../assets/knockout.js"), Asset("js", "knockout_punches", "/home/chfin/.julia/packages/Knockout/JE2Yq/src/../assets/knockout_punches.js"), Asset("js", nothing, "/home/chfin/.julia/packages/InteractBase/l8cEC/src/../assets/all.js"), Asset("css", nothing, "/home/chfin/.julia/packages/InteractBase/l8cEC/src/../assets/style.css"), Asset("css", nothing, "/home/chfin/.julia/packages/Interact/0klKX/src/../assets/bulma_confined.min.css")], Dict{Any,Any}("loading"=>Any[JSString("(function (val){return (val!=this.model[\"loading\"]()) ? (this.valueFromJulia[\"loading\"]=true, this.model[\"loading\"](val)) : undefined})")],"clicks"=>Any[JSString("(function (val){return (val!=this.model[\"clicks\"]()) ? (this.valueFromJulia[\"clicks\"]=true, this.model[\"clicks\"](val)) : undefined})")]), ConnectionPool(Channel{Any}(sz_max:9223372036854775807,sz_curr:0), Set(WebIO.AbstractConnection[]), Channel{WebIO.AbstractConnection}(sz_max:32,sz_curr:0)), WebIO.JSString[JSString("function () {\n    var handler = (function (ko, koPunches) {\n    ko.punches.enableAll();\n    ko.bindingHandlers.numericValue = {\n        init : function(element, valueAccessor, allBindings, data, context) {\n            var stringified = ko.observable(ko.unwrap(valueAccessor()));\n            stringified.subscribe(function(value) {\n                var val = parseFloat(value);\n                if (!isNaN(val)) {\n                    valueAccessor()(val);\n                }\n            })\n            valueAccessor().subscribe(function(value) {\n                var str = JSON.stringify(value);\n                if ((str == \"0\") && ([\"-0\", \"-0.\"].indexOf(stringified()) >= 0))\n                     return;\n                 if ([\"null\", \"\"].indexOf(str) >= 0)\n                     return;\n                stringified(str);\n            })\n            ko.applyBindingsToNode(element, { value: stringified, valueUpdate: allBindings.get('valueUpdate')}, context);\n        }\n    };\n    var json_data = {\"loading\":WebIO.getval({\"name\":\"loading\",\"scope\":\"knockout-component-8b327201-37a2-4b24-a15b-14a8838dff89\",\"id\":\"ob_17\",\"type\":\"observable\"}),\"clicks\":WebIO.getval({\"name\":\"clicks\",\"scope\":\"knockout-component-8b327201-37a2-4b24-a15b-14a8838dff89\",\"id\":\"ob_16\",\"type\":\"observable\"})};\n    var self = this;\n    function AppViewModel() {\n        for (var key in json_data) {\n            var el = json_data[key];\n            this[key] = Array.isArray(el) ? ko.observableArray(el) : ko.observable(el);\n        }\n        \n        \n        [this[\"loading\"].subscribe((function (val){!(this.valueFromJulia[\"loading\"]) ? (WebIO.setval({\"name\":\"loading\",\"scope\":\"knockout-component-8b327201-37a2-4b24-a15b-14a8838dff89\",\"id\":\"ob_17\",\"type\":\"observable\"},val)) : undefined; return this.valueFromJulia[\"loading\"]=false}),self),this[\"clicks\"].subscribe((function (val){!(this.valueFromJulia[\"clicks\"]) ? (WebIO.setval({\"name\":\"clicks\",\"scope\":\"knockout-component-8b327201-37a2-4b24-a15b-14a8

In [11]:
Polygrams.voicedist(matcherwdg[][3])

1

In [88]:
#include("../src/polygrams.jl")

Main.Polygrams

In [12]:
markwdg = Polygrams.markschemaswdg(notes, xml, [fonte2v[1:2,1:2]]; timesigs=timesigs[1])

WebIO.Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{DOM}(DOM(:html, :div), Any[Node{DOM}(DOM(:html, :div), Any[Scope("scope-8227e7c4-beb2-48b7-889b-dd3cad3e7fab", Node{DOM}(DOM(:html, :span), Any[], Dict{Symbol,Any}(), 0), Dict{String,Tuple{Observables.AbstractObservable,Union{Nothing, Bool}}}("selected"=>(Observable{Array{Any,1}} with 2 listeners. Value:
Any[], nothing),"highlights"=>(Observable{Array{Any,1}} with 1 listeners. Value:
Any[], nothing),"jumpto"=>(Observable{String} with 1 listeners. Value:
"", nothing),"input"=>(Observable{String} with 1 listeners. Value:
"<?xml version=\"1.0\" encoding=\"utf-8\"?>\n<!DOCTYPE score-partwise PUBLIC \"-//Recordare//DTD MusicXML 3.1 Partwise//EN\" \"http://www.musicxml.org/dtds/partwise.dtd\">\n<score-partwise version=\"3.1\">\n  <identification>\n    <encoding>\n      <software>MuseScore 3.1.0</software>\n      <encoding-date>2019-06-11</encoding-date>\n      <supports element=\"accidental\" type=\"yes\"/>\n      <supports element=\"beam\" type=\"yes\"/>\n      <supports element=\"print\" attribute=\"new-page\" type=\"yes\" value=\"yes\"/>\n      <supports element=\"print\" attribute=\"new-system\" type=\"yes\" value=\"yes\"/>\n      <supports element=\"stem\" type=\"yes\"/>\n      </encoding>\n    </identification>\n  <defaults>\n    <scaling>\n      <millimeters>6.4</millimeters>\n      <tenths>40</tenths>\n      </scaling>\n    <page-layout>\n      <page-height>1856.25</page-height>\n      <page-width>1312.5</page-width>\n      <page-margins type=\"even\">\n        <left-margin>62.5</left-margin>\n        <right-margin>62.5</right-margin>\n        <top-margin>62.5</top-margin>\n        <bottom-margin>125</bottom-margin>\n        </page-margins>\n      <page-margins type=\"odd\">\n        <left-margin>62.5</left-margin>\n        <right-margin>62.5</right-margin>\n        <top-margin>62.5</top-margin>\n        <bottom-margin>125</bottom-margin>\n        </page-margins>\n      </page-layout>\n    <word-font font-family=\"FreeSerif\" font-size=\"10\"/>\n    <lyric-font font-family=\"FreeSerif\" font-size=\"11\"/>\n    </defaults>\n  <credit page=\"1\">\n    <credit-words default-x=\"1250\" default-y=\"1693.75\" justify=\"right\" valign=\"bottom\" font-size=\"9.216\">S. #</credit-words>\n    </credit>\n  <credit page=\"1\">\n    <credit-words default-x=\"656.249\" default-y=\"1793.75\" justify=\"center\" valign=\"top\" font-size=\"7.488\">Mozart, KV 281</credit-words>\n    </credit>\n  <credit page=\"1\">\n    <credit-words default-x=\"656.249\" default-y=\"1793.75\" justify=\"center\" valign=\"top\" font-size=\"9\">- # -</credit-words>\n    </credit>\n  <part-list>\n    <score-part id=\"P1\">\n      <part-name print-object=\"no\">Klavier linke Hand</part-name>\n      <score-instrument id=\"P1-I1\">\n        <instrument-name/>\n        </score-instrument>\n      <midi-device id=\"P1-I1\" port=\"1\"/>\n      <midi-instrument id=\"P1-I1\">\n        <midi-channel>1</midi-channel>\n        <midi-program>1</midi-program>\n        <volume>78.7402</volume>\n        <pan>0</pan>\n        </midi-instrument>\n      </score-part>\n    </part-list>\n  <part id=\"P1\">\n    <measure number=\"0\" implicit=\"yes\" width=\"235.02\">\n      <print>\n        <system-layout>\n          <system-margins>\n            <left-margin>20.84</left-margin>\n            <right-margin>-0.00</right-margin>\n            </system-margins>\n          <top-system-distance>202.83</top-system-distance>\n          </system-layout>\n        <staff-layout number=\"2\">\n          <staff-distance>65.00</staff-distance>\n          </staff-layout>\n        </print>\n      <attributes>\n        <divisions>12</divisions>\n        <key>\n          <fifths>-2</fifths>\n          </key>\n        <time>\n          <beats>2</beats>\n          <beat-type>2</beat-type>\n          </time>\n        <staves>2</staves>\n        <clef number=\"1\">\n          <sign>G</sign>\n          <line>2</line>\n          </clef>\n        <clef nu

In [141]:
markwdg[:marked][]

SortedSet(Any[Array{TimedNote{SpelledInterval,Rational{Int64}},1}[[Note#note0<0//1-1//4>(F5), Note#note3<1//4-1//2>(B3)], [Note#note11<1//2-1//1>(C4), Note#note6<5//8-3//4>(E♭5)]]],
Base.Order.By{getfield(Main.Polygrams, Symbol("##109#121"))}(getfield(Main.Polygrams, Symbol("##109#121"))()))

poly = Array{TimedNote{SpelledInterval,Rational{Int64}},1}[[Note#note46<17//4-35//8>(F5), Note#note54<17//4-9//2>(B2)], [Note#note66<9//2-19//4>(C4), Note#note57<37//8-19//4>(E♭5)]]
map((s->begin
            #= /home/chfin/Uni/phd/code/schemata_code/src/autoannot.jl:235 =#
            map(id, s)
        end), poly) = Array{String,1}[["note46", "note54"], ["note66", "note57"]]
poly = Array{TimedNote{SpelledInterval,Rational{Int64}},1}[[Note#note0<0//1-1//4>(F5), Note#note3<1//4-1//2>(B3)], [Note#note11<1//2-1//1>(C4), Note#note6<5//8-3//4>(E♭5)]]
map((s->begin
            #= /home/chfin/Uni/phd/code/schemata_code/src/autoannot.jl:235 =#
            map(id, s)
        end), poly) = Array{String,1}[["note0", "note3"], ["note11", "note6"]]


In [ ]:
ratings = map(polys) do poly
    on, off = Polygrams.polyrange(poly)
    score = Polygrams.rate(poly,featurefs,[1, -1//12, -2])
    (onset=on, offset=off, score=score)
end
ratings[1]

In [ ]:
rt = Polygrams.ratingswdg(ratings, highlights=[ratings[[1,2,3,4]]])

In [ ]:
rt[:highlights][] = [ratings[[1000,2000,3000]]];

In [ ]:
data = Polygrams.polydensities(map(Polygrams.polyrange, polys))
Polygrams.polydensitywdg(data)

In [ ]:
include("../src/polygrams.jl")

In [ ]:
Polygrams.annotationview(pieceid, [fonte2v], featureweights)